### Helper methods

In [ ]:
# In this cell are some helper methods we'll use for our graphql queries in later cells...

from seeq import spy, sdk
import uuid
import json
from collections import defaultdict

# login only necessary if you are outside of Seeq Datalab
username = "username"
password ="password"
spy.login(username=username, password=password)

def execute(api, query, variables):
    result = api.graphql(body=sdk.GraphQLInputV1(query=query, variables=variables))
    if result.errors:
        raise RuntimeError(json.dumps(result.errors))
    else:
        return result.data      

def row(headers, r):
    return {
        header["name"]: value for header, value in zip(headers, r) if value is not None
    }


def table_iterator(tbl):
    return (row(tbl["headers"], r) for r in tbl["rows"] if any(value is not None for value in r))


def table(tbl):
    return list(table_iterator(tbl))

api = sdk.GraphQLApi(spy.client)

# There are two graphQl queries that we need to get the evidence and to get all the rest of the context... get_table and get_context

get_table = """
query GetTable($id: String!, $filter: FilterInput, $limit: Int!, $columnsToInclude: [String!]) {
  table(id: $id, filter: $filter, limit: $limit, columnsToInclude: $columnsToInclude) {
    rows
    headers {
      name
      type
    }
    hasMore
  }
}
"""

get_context = """
query Context($ids: [ContextIdInput!]!) {
  context(ids: $ids) {
    opaque {
      itemId
      datumId
      key
      context
      contextId
      createdAt
      updatedAt
      archived
      startTime
      endTime
    }
    comments {
      itemId
      datumId
      context
      contextId
      createdAt
      updatedAt
      archived
    }
    labels {
      itemId
      datumId
      context
      contextId
      createdAt
      updatedAt
      archived
      label
    }
  }
}
"""

### Sample Query for Evidence

In [18]:
EVIDENCE_COLUMNS = ["Start","End","Duration","Asset UUID","Asset","IsUncertain","Path","Suppressed","item id","Condition","datum id","created at","Updated At"]

variables = {
    "id": "0f04b073-35f1-f910-b0fc-f17d16505009", # YOUR TABLE ID HERE
    "limit": 100000,
    "columnsToInclude": EVIDENCE_COLUMNS,
    "filter": {"compositeFilter":{"filter1":
                                  {"compositeFilter":
                                   {"filter1":
                                    {"compositeFilter":
                                     {"filter1": {"valueFilter":{"columnName":"Start","filterType":"LESS_THAN_OR_EQUAL","value":2732224411815000000}},
                                      "filter2": {"compositeFilter":{"filter1":{"simpleFilter":{"columnName":"End","filterType":"IS_NULL"}},
                                                                     "filter2":{"valueFilter":{"columnName":"End","filterType":"GREATER_THAN_OR_EQUAL","value":1731619611815000000}},"operation":"OR"}},
                                      "operation":"AND"}},
                                    "filter2":{"valueFilter":{"columnName":"Updated At","filterType":"GREATER_THAN_OR_EQUAL","value":"1980-01-01T00:00:00.000Z"}},"operation":"AND"}},
                                  "filter2":{"simpleFilter":{"columnName":"Deleted at","filterType":"IS_NULL"}},"operation":"AND"}
              }
}


results = execute(api, get_table, variables)
evidence = table(results['table'])
evidence[:5]

[{'Start': 1749517200000000000,
  'End': 1749520800000000000,
  'Duration': 3600000000000,
  'IsUncertain': False,
  'Path': 'periods1',
  'Suppressed': False,
  'item id': '0F04B05D-6FB7-F9D0-A05D-FDDA7E88CB8B',
  'Condition': 'periods1',
  'datum id': '1749517200000000000',
  'created at': '2025-06-16T23:11:21.637637Z',
  'Updated At': '2025-06-16T23:11:21.637637Z'},
 {'Start': 1749524400000000000,
  'End': 1749528000000000000,
  'Duration': 3600000000000,
  'IsUncertain': False,
  'Path': 'periods1',
  'Suppressed': False,
  'item id': '0F04B05D-6FB7-F9D0-A05D-FDDA7E88CB8B',
  'Condition': 'periods1',
  'datum id': '1749524400000000000',
  'created at': '2025-06-16T23:11:21.637637Z',
  'Updated At': '2025-06-16T23:11:21.637637Z'},
 {'Start': 1749531600000000000,
  'End': 1749535200000000000,
  'Duration': 3600000000000,
  'IsUncertain': False,
  'Path': 'periods1',
  'Suppressed': False,
  'item id': '0F04B05D-6FB7-F9D0-A05D-FDDA7E88CB8B',
  'Condition': 'periods1',
  'datum id': '1

### Sample Query for EvidenceContext

In [19]:
EVIDENCE_CONTEXT_COLUMNS = ["item id","datum id", "context_labels.id","context_labels.label_name"]

START_FILTER_TIME = 1932224411815000000
END_FILTER_TIME = 1031619611815000000

variables = {
    "id": "0f04b073-35f1-f910-b0fc-f17d16505009", # YOUR TABLE ID HERE
    "limit": 100000, # I just set this to 10 to limit output within the notebook...
    "columnsToInclude": EVIDENCE_CONTEXT_COLUMNS,
    "filter": {
                 "compositeFilter":{"filter1":
                                  {"compositeFilter":
                                   {"filter1":
                                    {"compositeFilter":
                                     {"filter1": {"valueFilter":{"columnName":"Start","filterType":"LESS_THAN_OR_EQUAL","value":START_FILTER_TIME}},
                                      "filter2": {"compositeFilter":{"filter1":{"simpleFilter":{"columnName":"End","filterType":"IS_NULL"}},"filter2":{"valueFilter":{"columnName":"End","filterType":"GREATER_THAN_OR_EQUAL","value":END_FILTER_TIME}},"operation":"OR"}},
                                      "operation":"AND"}},
                                    "filter2":{"valueFilter":{"columnName":"Updated At","filterType":"GREATER_THAN_OR_EQUAL","value":"1980-01-01T00:00:00.000Z"}},"operation":"AND"}},
                                    "filter2":{"simpleFilter":{"columnName":"Deleted at","filterType":"IS_NULL"}},"operation":"AND"}
              }
}

"""
The logic in the above filter is as follows...
1. compositeFilter1...
    1. compositeFilter2...
        1. compositeFilter3...
          1. The start time is less than or equal to 
          2.
        2. 
    2. The "Delted At" column is NULL, meaning the context has not been archived.
"""


results = execute(api, get_table, variables)
details = table(results['table'])
details[:10] # The first 10 results.  Each result will be an item id / datum id pair along with any active context labels should they exist...

[{'item id': '0F04B05D-6FB7-F9D0-A05D-FDDA7E88CB8B',
  'datum id': '1749517200000000000'},
 {'item id': '0F04B05D-6FB7-F9D0-A05D-FDDA7E88CB8B',
  'datum id': '1749524400000000000'},
 {'item id': '0F04B05D-6FB7-F9D0-A05D-FDDA7E88CB8B',
  'datum id': '1749531600000000000',
  'context_labels.id': '0F04B062-8088-77A0-A360-E3166C6A6778',
  'context_labels.label_name': 'flag'},
 {'item id': '0F04B05D-6FB7-F9D0-A05D-FDDA7E88CB8B',
  'datum id': '1749538800000000000'},
 {'item id': '0F04B05D-6FB7-F9D0-A05D-FDDA7E88CB8B',
  'datum id': '1749546000000000000',
  'context_labels.id': '0F04B062-CCA0-7750-9385-8874EB7E73D5',
  'context_labels.label_name': 'reviewed'},
 {'item id': '0F04B05D-6FB7-F9D0-A05D-FDDA7E88CB8B',
  'datum id': '1749553200000000000'},
 {'item id': '0F04B05D-6FB7-F9D0-A05D-FDDA7E88CB8B',
  'datum id': '1749560400000000000'},
 {'item id': '0F04B05D-6FB7-F9D0-A05D-FDDA7E88CB8B',
  'datum id': '1749567600000000000'},
 {'item id': '0F04B05D-6FB7-F9D0-A05D-FDDA7E88CB8B',
  'datum id

### Sample Query for Context

In [20]:
results = execute(api, get_context, {"ids": []})

# There are three context tables in Seeq, comments, labels, and opaque.  I've included the query for all three in the get_context variable from the helpers cell above, but in reality, all of the information is actually available in opaque.
# Since you're primarily interested in the comments, to make it a little simpler to extract, we can merge the opaque and comments and datumID/labelId so that there is a field of comments context available on the results. 

# The graphql endpoint for Context doesn't have as much functionality around 'filtering' down as the table one, but you can just grab the whole thing and filter in code...

def merge_contexts(data):
    merged = defaultdict(dict)
    for kind in ['opaque', 'comments']:
        for context in data.get(kind, []):
            key_tuple = (context.get('itemId'), context.get('datumId'))
            adjusted_context = {}
            for k, v in context.items():
                if k in ('itemId', 'datumId'):
                    adjusted_context[k] = v
                elif k == 'context':
                    adjusted_context[f'{kind} context'] = v
                else:
                    adjusted_context[k] = v
            merged[key_tuple].update(adjusted_context)
    return list(merged.values())

merge_contexts(results['context'])[0:5]

[{'itemId': '0F04B05D-6FB7-F9D0-A05D-FDDA7E88CB8B',
  'datumId': '1749690000000000000',
  'key': 'vantage_metadatab48c4d7c-05bc-4271-8ead-f686875bdefa',
  'opaque context': '{"identifier":"notes","kind":"Capsule","kind_id":"1749690000000000000","starred":false,"seeq_context_ids":["0F04BA05-1907-EE80-866D-B21D790CA93A"],"related":"","content":{"value":"sdsdfsdfsd"},"serialized_extensions":[],"user_metadata":{"name":"ehsan shahidi","id":"0F04B006-B713-75B0-8137-7111960983EC"},"purview":{},"conditionMonitorId":"0F04B073-7738-FFE0-8479-41A27E8ACFD2"}',
  'contextId': '0F04BA05-1907-EE80-866D-B21D790CA93A',
  'createdAt': '2025-06-17T17:27:18.376199Z',
  'updatedAt': '2025-06-17T17:27:18.376199Z',
  'archived': False,
  'startTime': '2025-06-12T01:00:00Z',
  'endTime': '2025-06-12T02:00:00Z',
  'comments context': 'sdsdfsdfsd'},
 {'itemId': '0F04B05D-6FB7-F9D0-A05D-FDDA7E88CB8B',
  'datumId': '1749618000000000000',
  'key': 'vantage_metadatae4fc06e3-ef0e-4942-8d5f-5488b9af3ad0',
  'opaque c